In [352]:
#import nbpresent
import pandas as pd
import datetime as dt
import matplotlib.pyplot as plt
import matplotlib.dates as mdates
import numpy as np

from sklearn.feature_extraction import DictVectorizer
from sklearn.decomposition import PCA
from nltk.stem import PorterStemmer, WordNetLemmatizer
import nltk
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
from sklearn.metrics.pairwise import linear_kernel
import string
from nltk.corpus import stopwords
import math
from collections import Counter
nltk.download('stopwords')   

from gensim.models import Word2Vec

from bokeh.plotting import *
from bokeh.models import *
import matplotlib as mpl

[nltk_data] Downloading package stopwords to /Users/Jean-
[nltk_data]     BaptistePROST/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


## Preprocessing

In [3]:
def get_date(x):
    """from string to datatime.date()"""
    return dt.datetime.strptime(x, '%m/%d/%Y %H:%M').replace(minute=0, hour=0, second=0)

def cleaning_content(df,dataset,  right=True, left=True):
    df_tmp=df[df.language=='English'].drop(columns={'harvested_date', 'language'})
    df_tmp=df.loc[:,['publish_date','content', 'account_category']]

    #category
    if not left:
        df_tmp=df_tmp[(df_tmp.account_category=='RightTroll')]
    elif not right:
        df_tmp=df_tmp[(df_tmp.account_category=='LeftTroll')]
    else:        
        df_tmp=df_tmp[(df_tmp.account_category=='RightTroll') | (df_tmp.account_category=='LeftTroll')  ]

    #date 
    df_tmp['publish_date']=df_tmp.publish_date.apply(lambda x: get_date(x))
    df_tmp=df_tmp[df_tmp.publish_date > dt.datetime(2014,10,1,0,0,0)].drop(columns='publish_date') #selecting after Oct 2014

    df_tmp['dataset']=dataset #from which dataset it comes

    return df_tmp

In [4]:
data='Data/russian-troll-tweets/IRAhandle_tweets_'
    
df=pd.DataFrame()
for dataset in range(1,9):
    df_tmp=cleaning_content(pd.read_csv(data+str(dataset)+'.csv'), dataset)
    df=df.append(df_tmp, ignore_index=True)

In [171]:
df.head()

content account_category  dataset
0  "We have a sitting Democrat US Senator on tria...       RightTroll        1
1  Marshawn Lynch arrives to game in anti-Trump s...       RightTroll        1
2  Daughter of fallen Navy Sailor delivers powerf...       RightTroll        1
3  JUST IN: President Trump dedicates Presidents ...       RightTroll        1
4  19,000 RESPECTING our National Anthem! #StandF...       RightTroll        1

In [157]:
link_numbers=('http', '0', '1', '2', '3', '4', '5', '6', '7', '8', '9', '-')
stemmer = PorterStemmer()
stop_w=[word.replace('\'','') for word in stopwords.words('english')]+ ['', '&amp', 'amp','rt']

def tokenize(text): #__call__
    text_cleaned = ''.join(ch for ch in text if ch not in '#!"$%&\()*+,./:;<=>?@[\\]^_{|}~\'').split(' ') 
    
    words= [word.lower().encode('ascii',errors='ignore').decode() for word in text_cleaned \
            if not ( (word.startswith(link_numbers)) | (word.endswith(link_numbers)) )]
    
    words=[stemmer.stem(word) for word in words if word not in stop_w ]
    
    if len(words) > 0:
        return words
    else: #tweets that contains only links or emojiis ...
        pass

def top_vocabulary(text, top=10):
    words = [stemmer.stem(word) for word in tokenize(text) if word not in stop_w] 
    voc=pd.DataFrame.from_dict(Counter(words), orient='index')\
            .rename(columns={0:'Count'})\
            .sort_values(by='Count', ascending=False)[:top]
    return voc

In [181]:
df['Clean_tweet']=df.apply(lambda row: tokenize(row['content']), axis=1 )

## Model Creation

In [440]:
def word_orientation(df, vocab,):
    tot_words=len(vocab)
    words_party= pd.DataFrame(np.zeros(tot_words), columns={'Score'},index=vocab)

    voc=[]
    for tweet in df[(df.Clean_tweet.isnull()==False) & (df.account_category=='RightTroll')].Clean_tweet:
        voc+=tweet
    count=pd.DataFrame.from_dict(Counter(voc), columns={'R'}, orient='index')

    words_party=words_party.merge(count, how='left', right_index=True, left_index=True)

    voc=[]
    for tweet in df[(df.Clean_tweet.isnull()==False) & (df.account_category=='LeftTroll')].Clean_tweet:
        voc+=tweet
    count=pd.DataFrame.from_dict(Counter(voc), columns={'L'}, orient='index')

    words_party=words_party.merge(count, how='left', right_index=True, left_index=True)
    words_party.fillna(0,inplace=True)
    words_party['Score']=words_party.apply(lambda row: (row['R']-row['L'])/(row['R']+row['L']), axis=1)

    return words_party

In [447]:
#non empty clean tweet
tweets=df[df.Clean_tweet.isnull()==False]['Clean_tweet']
model = Word2Vec(tweets.tolist(), min_count=10, size=1000)

In [448]:
print(model)

Word2Vec(vocab=31377, size=1000, alpha=0.025)


In [449]:
# fit a 2d PCA model to the vectors
X = model.wv.vectors
pca = PCA(n_components=3)

result = pca.fit_transform(X)
result = pd.DataFrame(pca.fit_transform(X), columns={'X','Y','Z'})
result.index=list(model.wv.vocab)
result=result.merge(word_orientation(df,model.wv.vocab), how='left', right_index=True, left_index=True)
result['colors'] = [
    "#%02x%02x%02x" % (int(r), int(g), int(b)) for r, g, b, _ in 255*mlp.cm.coolwarm(mpl.colors.Normalize()(result['Score'].tolist()))
]

In [450]:
result.head()

X         Z         Y     Score        R        L   colors
sit       5.681784  2.544261  0.423766  0.020845    906.0    869.0  #dfdbd9
democrat  7.450650 -1.909349  0.192623  0.795162  13654.0   1558.0  #d75444
us        7.241748 -1.101061 -4.065220  0.350144  28218.0  13582.0  #f7b598
senat     6.546263  2.002624  0.896359  0.661033   7027.0   1434.0  #e7755c
trial     4.593181 -1.706919 -3.946059  0.070137    740.0    643.0  #e5d8d0

vocab=list(model.wv.vocab)
tot_words=len(vocab)
words_party= pd.DataFrame(np.zeros(tot_words), columns={'Score'},index=vocab)

voc=[]
for tweet in df[(df.Clean_tweet.isnull()==False) & (df.account_category=='RightTroll')].Clean_tweet:
    voc+=tweet
count=pd.DataFrame.from_dict(Counter(voc), columns={'R'}, orient='index')

words_party=words_party.merge(count, how='left', right_index=True, left_index=True)

voc=[]
for tweet in df[(df.Clean_tweet.isnull()==False) & (df.account_category=='LeftTroll')].Clean_tweet:
    voc+=tweet
count=pd.DataFrame.from_dict(Counter(voc), columns={'L'}, orient='index')

words_party=words_party.merge(count, how='left', right_index=True, left_index=True)
words_party.fillna(0,inplace=True)
words_party['Score']=words_party.apply(lambda row: (row['R']-row['L'])/(row['R']+row['L']), axis=1)


## Plotting:

In [451]:
p = figure(plot_width=850, plot_height=450) # x_axis_type='datetime')
p.title.text = 'Tweets topic clusters'

source = ColumnDataSource(data=result)
p.scatter(x='X', y='Y', source=source, fill_color='colors', fill_alpha=0.6, line_color=None)

p.legend.location = 'top_left'
p.legend.click_policy='hide'

hover_tool=tools.HoverTool(
    tooltips=[('Word', '@index'), 
             ('Orientation', '@Score')],
    formatters={'index' : 'printf', 'Score' : 'printf' },
    mode='mouse'
)

p.tools.append(hover_tool)
output_notebook()#\interactive_legend.html\)# title=\interactive_legend.py example\)\n

Loading BokehJS ...

In [452]:
show(p)

In [453]:
 #interactive plot
p = figure(plot_width=850, plot_height=450) # x_axis_type='datetime')
p.title.text = 'Tweets topic clusters'


source_ = ColumnDataSource(data=result)
#colors=[colormap[x] for x in flowers['species']]
p.scatter(x='Y', y='Z', source=source_, fill_color='colors', fill_alpha=0.6, line_color=None)

p.legend.location = 'top_left'
p.legend.click_policy='hide'

hover_tool=tools.HoverTool(
    tooltips=[('Word', '@index')],
    formatters={'index' : 'printf', },
    mode='mouse'
)

p.tools.append(hover_tool)
output_notebook()#\interactive_legend.html\)# title=\interactive_legend.py example\)\n

Loading BokehJS ...

In [454]:
show(p)

In [366]:
model.most_similar("macron")

/Users/Jean-BaptistePROST/miniconda3/envs/ada/lib/python3.6/site-packages/ipykernel_launcher.py:1: DeprecationWarning: Call to deprecated `most_similar` (Method will be removed in 4.0.0, use self.wv.most_similar() instead).
  """Entry point for launching an IPython kernel.


[('emmanuel', 0.6755629777908325),
 ('lepen', 0.6367908716201782),
 ('holland', 0.6229581832885742),
 ('frenchelect', 0.5985648036003113),
 ('aunomdupeupl', 0.5625836253166199),
 ('pen', 0.5509232878684998),
 ('franc', 0.5447674989700317),
 ('french', 0.5375246405601501),
 ('fillon', 0.5292798280715942),
 ('le', 0.5005808472633362)]

In [457]:
model.accuracy(most_similar=)

/Users/Jean-BaptistePROST/miniconda3/envs/ada/lib/python3.6/site-packages/ipykernel_launcher.py:1: DeprecationWarning: Call to deprecated `accuracy` (Method will be removed in 4.0.0, use self.wv.accuracy() instead).
  """Entry point for launching an IPython kernel.


TypeError: accuracy() missing 1 required positional argument: 'questions'